# Genetic Algorithms

In this assignment you will be cracking a Vigenere cipher with genetic algorithms. Recall from lecture that Genetic Algorithms are variants of beam search with two operators, crossover and mutation, that mimic the evolutionary process of natural selection. Generally, the algorithm starts with a population and allows the highest fitness individuals to mate with one another to populate the next generation. This process stops when some individual is fit enough or if enough time has elapsed. You can reference Chapter 4 in the textbook (p.119) and the lecture notes [here](http://www.cs.cornell.edu/courses/cs4700/2019fa/lectures/Lecture5.pdf) to learn more. 


## The Vigenere Cipher

You will be using GA to learn the keyword of a Vigenere cipher given a plaintext string in English, and the same string encrypted with the Vigenere cipher. We include some sample encrypted sentences, and if your algorithm runs correctly you should be able to read the original messages!

### Example
A [Vigenere cipher](https://en.wikipedia.org/wiki/Vigen%C3%A8re_cipher) shifts letters in a message based on a keyword. Let's use the keyword is "ALICE" to encrypt the plaintext 

> Why, sometimes I've believed as many as six impossible things before breakfast!

First, we *encode* each letter in the key and the sentence into integers (e.g. A=0, B=1, and so on) to make it easier to work with. Note that the punctuation, spaces, and other non-alphabetic characters are preserved, since the Vigenere cipher doesn't affect them. For this assignment, we also ignore letter cases. (The example below has been truncated after the word "believed".)

`[22, 7, 24, ',', ' ', 18, 14, 12, 4, 19, 8, 12, 4, 18, ' ', 8, "'", 21, 4, ' ', 1, 4, 11, 8, 4, 21, 4, 3, ...]`

Likewise, "ALICE" is encoded as `[0, 11, 8, 2, 4]`.

To apply the cipher, we add 0 to the first letter in the message, 11 to the second letter, and so on. (If the resulting sum is greater than 26, we take it mod 26.) When we reach the end of the keyword, we go back to its beginning. So, after encrypting, we get:

`[22, 18, 6, ',', ' ', 20, 18, 12, 15, 1, 10, 16, 4, 3, ' ', 16, "'", 23, 8, ' ', 1, 15, 19, 10, 8, 21, 15, 11 ...]`

which represents the ciphertext 

> WSG, USMPBKQED Q'XI BPTKIVPL

To read this message, we first need to encode the text, decrypt the numbers, and then encode the decrypted message to get back

> WHY, SOMETIMES I'VE BELIEVED

## Genetic Algorithms: Cracking the Vigenere Cipher Key

To crack the cipher, we will be finding the key. We are provided with

1. The ciphertext
2. The plaintext
3. The length of the key

Each possible key that we will be working with will be encoded as a chromosome, and the fitness function will evaluate how close the candidate chromosome can get to the true key when decrypting the given ciphertext.

## Conceptual Pre-Questions [10 points]
Fill out the answer below the question in its cell. 


**What is a chromosome (in the context of genetic algorithms)? In this project, what does a chromosome represent?**

###YOUR SOLUTION HERE

**What is crossover?**

###YOUR SOLUTION HERE

**What are some ways in which we could modify the population every iteration?**

###YOUR SOLUTION HERE

## Coding [80 points] 
Below, you will be expected to write code where you see `### YOUR SOLUTION HERE`. 

You will be asked to implement the following functions:
- `init_population(POPN_SIZE, KLEN)`: takes in an `integer` representing the number of individuals in the initial population, and an `integer` representing the length of the key we're looking for. The initial population should be made up of individuals, represented by their chromosomes.
- `fitness(chrom, cipher, plain)`: takes in a `list` representing the chromosome (key), a `list` representing the ciphertext, and a `list` representing the true plaintext. The fitness score returned should evaluate the individual's chromosome based on how well it decrypts the ciphertext.
- `crossover(parents)`: takes in a `list` of pairs of parents. The paired parents mate and create offspring with random parts of parent 1 and parent 2. 
- `mutate(parent, rate)`: takes in a `list` representing the chromosome (key) and a `float` between 0 and 1 inclusive as the mutation rate. Hint: look at the numpy.random documentation to use the mutation rate to choose whether or not to mutate a letter.


When you implement genetic algorithms, the design of the chromosome is crucial. It determines how the space of models that GA will explore, so it cannot be too complex while still capturing enough information to represent the space we're searching. 

For our implementation, we will only be using a simple 3-integer list to represent our keyword. Each number represents a character in the key. For example, "KEY" = `[10, 4, 24]`

### Imports

In [ ]:
import heapq as hq
import random
import numpy as np

### Helper functions
The functions below will be used in our provided code to set up the cipher. As explained above, we need to encode, then encrypt/decrypt, then decode to go from ciphertext to plaintext or vice versa. You will need to use at least one of the functions below to implement GA.

In [ ]:
def encode(text):
    '''
    Converts an English word to a list of numbers and nonalphabetic characters
    Leaves spaces and punctuation as characters
    Maps letters to their 0-indexed position in the alphabet
    i.e. A-> 0, b -> 1, Z -> 1
                
    text:   a string of characters
    enc:    the string encoded as integers in [0,26] with nonalphabetic chars
    '''
    enc = text.upper()
    getindex = lambda c: ord(c) - ord('A') if c.isupper() else c
    enc = [getindex(a) for a in enc]
    return enc

In [ ]:
def decode(enc):
    '''
    Converts a list of numbers [0,26] and characters to 
    the string they represent.
    
    enc:    the list of integers in [0,26] and characters 
    text:   the string that the encoded numbers represent
    '''
    
    getchars = lambda c: chr(c + ord('A')) if isinstance(c,int) else c
    dec = ''.join([getchars(c) for c in enc])
    
    return dec

In [ ]:
def encrypt(chrom, plain):
    '''
    Encrypt cipher using the key. 
            
    chrom:  the key that we are testing
    plain:  the encoded message that we want to encrypt using `chrom`
    
    Returns cipher: the encrypted, encoded message of `cipher` using `chrom` as a vigenere key
    '''
    K = len(chrom)
    cipher = []
    
    keycount = 0
    for i,c in enumerate(plain):
        if isinstance(c,int):
            cipher.append((c + 26 + chrom[keycount]) % 26)
            keycount = (keycount + 1) % K # look at the next letter of the key
        else:
            cipher.append(c)
    
    return cipher

In [ ]:
def decrypt(chrom, cipher):
    '''
    Decrypt cipher using the key. 
            
    chrom:  the key that we are testing
    cipher: the ciphertext that we want to decrypt using `chrom`

    Returns plain:  the plaintext we obtain by using the `chrom` key to decrypt `cipher`
    '''
    chrom = [-1 * c for c in chrom]
    plain = encrypt(chrom, cipher)
    return plain

Below is another helper function that gets random pairs from a population, used for crossover.

In [ ]:
def getpairs(population):
    '''    
    Return a list of pairs drawn from the population without replacement.
    Sets up the "parents" for a crossover step later. Returns n pairs 
    if population is size 2n or 2n+1.
                
    population: A list of chromosomes from which to choose parents
    pairs:      A list of pairs of chromosomes
    '''
    popnsize = len(population)
    numpairs = popnsize//2
    idx = np.random.choice(popnsize, (numpairs,2),replace=False)
    pairs = [(population[x], population[y]) for (x,y) in idx]
    return pairs
        

### Demonstration of Encoding/Decoding and Encrypting/Decrypting

The code below implements the Vigenere explanation at the top of the notebook. Feel free to walk through it to get an understanding of how we go from English, to numbers, to back.

In [ ]:
msg = "Why, sometimes I've believed"
enco = encode(msg)
print("encoded msg:\n",enco)

key = "ALICE"
chrom = encode(key)
print("chromosome\n",chrom)

encr = encrypt(chrom,enco)
print("encrypted, encoded\n",encr)

ciphertext = decode(encr)
print("text of encrypted, encoded\n",ciphertext)

decr = decrypt(chrom,encr)
print("decrypted:\n",decr)

deco = decode(decr)
print("text of decrypted msg:\n",deco)

### Implementing Genetic Algorithms [80 pts]

#### Initialize Population [20 pts]

Implement the `init_population` function that creates a population of individuals, or keys that are potential solutions to the Vigenere cipher. The initial population should contain `POPN_SIZE` individuals and generally is created as randomly as possible.

In [ ]:
def init_population(POPN_SIZE, KLEN):
    '''
    Creates a list of POPN_SIZE chromosomes, representing 
    individuals in the initial population.
            
    POPN_SIZE: the number of individuals in our initial population.
    KLEN:      the size of the key which we're searching for
    '''
    init_pop = []
    
    ###YOUR SOLUTION HERE
    return init_pop

#### Fitness [20 pts]

Implement the fitness function that will allow us to evaluate how fit an individual is. Given the chromosome, ciphertext, and correct plaintext, the fitness score should allow us to determine how close the plaintext generated from 'chrom' matches the correct plaintext. Note that the fitness score should be some percentage of the total length of the ciphertext.

In [ ]:
def fitness(chrom, cipher, plain): 
    '''
    Returns the fitReturnsness score of a chromosome.
            
    chrom:   the chromosome containing the key we want to test
    cipher:  the ciphertext that we want to decrypt
    plain:   the correct plaintext of 'ciphertext'
    '''
    score = 0
    ###YOUR SOLUTION HERE
    return score / len(ciphertext)

#### Crossover [20 pts]

The crossover function is how our algorithm makes progress towards predicting the cipher key. It takes two parents and crosses their genes to produce a child chromosome with some letters from parent 1 and some letters from parent 2. For example, the keywords 'cold' and 'barn' can mate to produce 'corn' ('co' + 'rn'). There are multiple ways to implement crossover. In the textbook it shows that you can pick a pivot point and select the beginning of parent 1, combining it with the end of parent 2. You could also randomly select a gene from parent 1 or 2 at each index, so 'care' and 'loan' can still cross to become 'corn'.

In [ ]:
def crossover(parents):
    """ 
    Takes in a list of pairs of parents. The paired parents mate and generate offspring chromosomes 
    with random parts of parent 1 and random parts of parent 2.
    
    Preconditions: parents is a list of pairs (2-entry tuples) of valid chromosomes (lists). Ex: [(p1,p2),(p3,p4)],
    where p1..p4 are lists of ints in 0..25 or punctuation characters (comma, apostrophe, space, etc.)
    
    Returns children: List of children chromosomes
    """
    children = []
    ###YOUR SOLUTION HERE
    return children

#### Mutation [20 pts]

However, what if no parents have 'c' as the first letter? If we only have chromosomes representing 'tarp' and 'torn', then no crossover of the chromosomes will ever produce 'corn' because there is no 'c' at index 0. This is where mutation comes in: 'tarp' might mutate to become 'carp' and then cross with 'torn' to finally produce 'corn'. Mutations usually occur at a low rate, but they provide variety in the "gene pool" to ensure that there are enough different chromosomes to find the message. If all of the chromosomes are too similar, the message may never be found. 

In [ ]:
def mutate(parent, rate=.1):
    """ 
    Takes in a list representing the parent chromosome and a float between 0 and 1 inclusive as the mutation rate.
    For each element of the list: with probability equal to "rate", mutate" it (in other words, change it to a
    random number between 0 and 25, inclusive). Otherwise, do nothing.

    Preconditions: parent is a list that represents a single chromosome (key).
            
    parent: The chromosome to mutate
    rate:   The probability that any given gene will be mutated
    
    Returns child:  The returned chromosome 
    """
    child = parent
    ###YOUR SOLUTION HERE
    return child


### Putting it all together 

Finally, we run it all! If your previous functions were implemented correctly, this should run for several iterations before returning a "decent" key for decrypting the sample texts in the **Demonstration** section below.

In [ ]:
def run_ga(ciphertext, plaintext, KLEN, verbose=False, POPN_SIZE=1000, ELITES=50, DROPS=500):
    '''
    Put it all together. Run GA with our specified chromosomes to find
    the key to the Vigenere cipher.
                
    ciphertext: A string containing the encrypted text message, in English characters 
    plaintext:  A string containing the decrypted text message, in English
    verbose:    Debug parameter; set true to print the running best chromosome
    POPN_SIZE:  The size of the initial population 
    KLEN:       The length of the key which we are searching for
    ELITES:     The number of best-scoring chromosomes to preserve each iteration
    DROPS:      The numer of wost-scoring chromosomes to drop each iteration
    
    Returns a chromosome that decrypts ciphertext into plaintext with good accuracy. 
        
    '''
    popn = init_population(POPN_SIZE,KLEN)
    print(popn[1])
    generations = 0
    cipher = encode(ciphertext)
    plain = encode(plaintext)
    scores = [(fitness(chrom,cipher,plain),chrom) for chrom in popn]
    bestscore = max(scores, key=lambda x: x[0])
    
    while generations < 1000:
        generations += 1
        bestscore = max(scores, key=lambda x: x[0])        
        if verbose:
            print("Accuracy: %4.3f%%\tBest chromosome: %r" % (bestscore[0]*100, bestscore[1]))
        # End if current chromosome is quite accurate
        if bestscore[0] > 0.80:
            return bestscore
            break
            
        # remembers chromosomes with the best scores, # = ELITES
        elites = hq.nlargest(ELITES, scores, key=lambda x: x[0])
                
        # drops chromosomes below a certain threshold
        scores = list(filter(lambda x:x[0] > 0.6, scores))   
        
        # pad up the population with random chromosomes to preserve population size
        topad = POPN_SIZE - ELITES - len(scores) # we'll be adding back the elites later
        padding = init_population(topad,KLEN)
        scores += [(fitness(chrom,cipher,plain),chrom) for chrom in padding] 
        
        # then drops the worst DROPS chromosomes
        for i in range(DROPS):
            scores.remove(min(scores,key=lambda x: x[0]))
  
        # strips away the scores of the population before crossover/mutation
        popn = [x[1] for x in scores]
        
        # crossover random pairs of the population
        children = crossover(getpairs(popn))
        
        # Since half the children disappear per iteration,
        # we run crossover twice on different parents in order to 
        # preserve population size
        children += crossover(getpairs(popn))

        # mutate the new population
        children = [mutate(c,0.1) for c in children]
        
        # calculate the scores of the new population
        scores = [(fitness(chrom,cipher, plain),chrom) for chrom in popn]
        
        # adds back the elites to the new pool of children
        scores += elites    
    
    return None

## Demonstration

First, we need to download the file that we will be looking at. 

In [ ]:
! rm -rf a1-data
! git clone https://github.com/cs4700-2019fa-data/a1-data/

#### Example 1: 3-character key

In [ ]:
with open('a1-data/lobster.txt', encoding='utf8') as f:
    plaintext = f.read()
enco = encode(plaintext) 

key = "KEY"
KLEN = len(key)
chrom = encode(key)
print("Actual key:",chrom)

encr = encrypt(chrom,enco)
ciphertext = decode(encr)

In [ ]:
score,ga_chrom = run_ga(ciphertext, plaintext, KLEN, True)

In [ ]:
decr = decrypt(ga_chrom,encr)
deco = decode(decr)
print("text of decrypted msg:\n",deco)

#### Example 2: 5-character key

In [ ]:
with open('a1-data/lobster.txt', encoding='utf8') as f:
    plaintext = f.read()
enco = encode(plaintext) 
# print("encoded msg:\n",enco)

key = "ALICE"

KLEN = len(key)
chrom = encode(key)
print("Actual key:",chrom)

encr = encrypt(chrom,enco)
# print("encrypted, encoded\n",encr)

ciphertext = decode(encr)
# print("text of encrypted\n",ciphertext)

In [ ]:
score,ga_chrom = run_ga(ciphertext, plaintext, KLEN, True)

In [ ]:
decr = decrypt(ga_chrom,encr)
deco = decode(decr)
print("text of decrypted msg:\n",deco)

## Conceptual Post-Questions [10 points]

**Is GA complete? Is GA optimal? What is its runtime and space complexity?**

###YOUR SOLUTION HERE

**How does changing the mutation rate affect the convergence of GA?**

###YOUR SOLUTION HERE

## Extra Credit [for karma!]

**It is actually very easy to find the Vigenere keyword directly, given an encrypted string and its decrypted version. How would you get the encoded keyword given the encoded ciphertext $c$ and encoded plaintext $p$ in O(length of key) time?**

###YOUR SOLUTION HERE

**Now, imagine we are solving the problem without access to the plaintext; we only know the ciphertext. The fitness function used above would no longer be feasible. What might be a way to use genetic algorithms to find a Vigenere keyword if you're only given the ciphertext, the maximum length of the keyword, and the fact that the original plaintext was in English?**

###YOUR SOLUTION HERE